# Práctica 3
### Equipo:
- Gutiérrez Pérez Gabriela G.
- Loeza Saldaña Sebastián.
- Ramos García Luis Gerardo.
- Rico Mendoza Josué.

In [1]:
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import spacy
import tkinter as tk
from tkinter import ttk, messagebox, filedialog, simpledialog
import os
import pickle
from tqdm import tqdm  
import time
import csv 

## Normalize

In [ ]:
# Cargar modelo de Spacy
nlp = spacy.load('es_core_news_sm')

articulos = {'el', 'la', 'los', 'las', 'un', 'una', 'unos', 'unas'}

preposiciones = {
    'a', 'ante', 'bajo', 'cabe', 'con', 'contra', 'de', 'desde', 'durante', 'en', 'entre', 'hacia', 'hasta', 'mediante',
    'para', 'por', 'según', 'sin', 'so', 'sobre', 'tras', 'versus', 'vía'
}

conjunciones = {
    'y', 'e', 'ni', 'que', 'o', 'u', 'pero', 'mas', 'sino', 'aunque', 'si', 'como', 'porque', 'pues', 'ya', 'luego',
    'así', 'bien', 'sea', 'fuera', 'bien', 'cuando', 'donde'
}

pronombres = {
    'yo', 'tú', 'él', 'ella', 'nosotros', 'nosotras', 'vosotros', 'vosotras', 'ellos', 'ellas', 'me', 'te', 'se', 'nos', 
    'os', 'mi', 'mis', 'tu', 'tus', 'su', 'sus', 'nuestro', 'nuestra', 'nuestros', 'nuestras', 'vuestro', 'vuestra', 
    'vuestros', 'vuestras', 'mío', 'mía', 'míos', 'mías', 'tuyo', 'tuya', 'tuyos', 'tuyas', 'suyo', 'suya', 'suyos', 
    'suyas', 'le', 'les', 'lo', 'la', 'los', 'las', 'él', 'ella', 'ellos', 'ellas', 'esto', 'estos', 'esta', 'estas',
    'eso', 'esos', 'esa', 'esas', 'aquel', 'aquellos', 'aquella', 'aquellas', 'quien', 'quienes', 'cual', 'cuales', 
    'cuya', 'cuyo', 'cuyas', 'cuyos'
}

stopWords = articulos | preposiciones | conjunciones | pronombres


def normalize_text(row, column_name, stop_words):
    try:
        text = row[column_name]
        doc = nlp(text)

        normalized_tokens = [ token.lemma_ for token in doc if token.text.lower() not in stop_words]
        return ' '.join(normalized_tokens)
    
    except Exception as e:
        print(f'No se pudo normalizar el {column_name} en el índice {row.name}: {e}')
        return None


## Función para cargar y normalizar el CSV

def load_and_normalize_csv(file_path):
    try:
        df = pd.read_csv(file_path)

        # Crear una ventana de progreso
        progress_window = tk.Toplevel()
        progress_window.title("Normalizando Datos")
        progress_window.geometry("300x100")

        progress_bar = ttk.Progressbar(progress_window, orient="horizontal", length=200, mode="determinate")
        progress_bar.pack(pady=20)

        progress_label = tk.Label(progress_window, text="")
        progress_label.pack()

        # Reemplazar valores NaN con cadenas vacías
        df['Title'] = df['Title'].fillna('')
        df['Content'] = df['Content'].fillna('')

        # Normalizar texto con barra de progreso y mensajes
        total_rows = len(df)
        total_steps = total_rows * 4  # Total de pasos (4 etapas por fila)
        current_step = 0

        # Definir los mensajes
        messages = ["Tokenizando...", "Lematizando...", "Eliminando Stopwords...", "Concatenando...", "Guardando CSV..."]

        for i, row in tqdm(df.iterrows(), total=total_rows, desc="Normalizando Data", unit="rows", leave=False):
            for message_index in range(5):  # 4 etapas por cada fila

                # Calcular el porcentaje actual
                current_progress = (current_step / total_steps) * 100
                
                # Mostrar el mensaje correspondiente según el progreso
                if 0 <= current_progress < 20:
                    progress_label.config(text=messages[0])
                elif 20 <= current_progress < 40:
                    progress_label.config(text=messages[1])
                elif 40 <= current_progress < 60:
                    progress_label.config(text=messages[2])
                elif 60 <= current_progress <= 80:
                    progress_label.config(text=messages[3])
                elif 80 <= current_progress <= 100:
                    progress_label.config(text=messages[4])

                # Actualizar la barra de progreso y la ventana
                progress_bar['value'] = current_progress
                progress_window.update()

                # Actualizar el paso actual
                current_step += 1

            # Lógica de normalización (se puede simplificar)
            df.loc[i, 'Title'] = normalize_text(row, 'Title', stopWords)
            df.loc[i, 'Content'] = normalize_text(row, 'Content', stopWords)

        # Una vez completado el proceso
        progress_label.config(text="Guardando CSV normalizado...")
        progress_bar['value'] = 100
        progress_window.update()

        # Guardar el archivo CSV normalizado
        normalized_file_path = file_path.replace(".csv", "_normalized.csv")
        df.to_csv(normalized_file_path, index=False)

        # Cerrar la ventana de progreso
        progress_window.destroy()

        # Mostrar mensaje de éxito
        messagebox.showinfo("Éxito", f"Archivo normalizado guardado en: {normalized_file_path}")
        return normalized_file_path
    except Exception as e:
        # Manejar cualquier error
        messagebox.showerror("Error", f"No se pudo procesar el archivo: {e}")
        return None


# Vectorization

In [3]:

# Función para generar representaciones vectoriales
def generate_vector_representations(data, vector_type, ngram_range):
    vectorizers = {
        "frequency": CountVectorizer(token_pattern= r'(?u)\w+|\w+\n|\.|\¿|\?', ngram_range=ngram_range),
        "binary": CountVectorizer(token_pattern= r'(?u)\w+|\w+\n|\.|\¿|\?', ngram_range=ngram_range, binary=True),
        "tfidf": TfidfVectorizer(token_pattern= r'(?u)\w+|\w+\n|\.|\¿|\?', ngram_range=ngram_range)
    }
    vectorizer = vectorizers.get(vector_type)
    vectorized_data = vectorizer.fit_transform(data)
    return (vectorizer,pd.DataFrame(vectorized_data.toarray(), columns=vectorizer.get_feature_names_out()))

# Vectorización del corpus para Title, Content y Title + Content
def vectorize_corpus(df):
    df.fillna("", inplace=True)
    df['Title_Content'] = df['Title'] + " " + df['Content']

    cols = ['Title', 'Content', 'Title_Content']
    vector_types = ['unigram_frequency', 'unigram_binary', 'unigram_tfidf', 
                    'bigram_frequency', 'bigram_binary', 'bigram_tfidf']

    ngram_ranges = {'unigram': (1, 1), 'bigram': (2, 2)}
    vectorizations = {col: {} for col in cols}
    
    for col in cols:
        for vec_type in vector_types:
            ngram = 'unigram' if 'unigram' in vec_type else 'bigram'
            type_name = vec_type.split('_')[1]
            vectorizations[col][vec_type] = generate_vector_representations(df[col], type_name, ngram_ranges[ngram])
    
    return vectorizations

# Función para guardar todas las representaciones en archivos PKL
#def save_all_vectorizations_to_pkl(vectorizations,carpeta):
#    for col, reps in vectorizations.items():
#        for vec_type, info in reps.items():
#            file_name = f"{col}_{vec_type}.pkl".replace('_', '-')
#            vector_file = open (file_name,'wb')
#            pickle.dump(info[0], vector_file)
#            #info[0].to_pickle(file_name)  # Guardar el DataFrame como archivo PKL
#            print(f"Archivo guardado: {file_name}")
#
#    messagebox.showinfo("Éxito", "Las representaciones se han guardado en archivos PKL.")

import os
import pickle
from tkinter import messagebox

def save_all_vectorizations_to_pkl(vectorizations, carpeta):
    # Asegurarse de que la carpeta existe, aunque ya debería haber sido creada previamente
    if not os.path.exists(carpeta):
        os.makedirs(carpeta)
    
    # Guardar los archivos en la carpeta especificada
    for col, reps in vectorizations.items():
        for vec_type, info in reps.items():
            # Crear el nombre del archivo
            file_name = f"{col}_{vec_type}.pkl".replace('_', '-')
            # Crear la ruta completa del archivo, dentro de la carpeta
            file_path = os.path.join(carpeta, file_name)
            
            # Guardar el archivo en la ruta especificada
            with open(file_path, 'wb') as vector_file:
                pickle.dump(info[0], vector_file)
            
            print(f"Archivo guardado: {file_path}")

    # Mostrar mensaje de éxito al usuario
    messagebox.showinfo("Éxito", "Las representaciones se han guardado en archivos PKL.")



# Recuperación de archivos similares

In [4]:
import math 

def cosine(x, y):
    val = sum(x[index] * y[index] for index in range(len(x)))
    print("val: ",str(val))
    sr_x = math.sqrt(sum(x_val**2 for x_val in x))
    print("x: ",str(sr_x))
    sr_y = math.sqrt(sum(y_val**2 for y_val in y))
    print("y: ",str(sr_y))
    res = val / (sr_x * sr_y)
   
    # Verificar si alguno de los vectores tiene magnitud 0
    if sr_x == 0 or sr_y == 0:
        return 0  # Similaridad de coseno es 0 si alguno es un vector nulo
    # Calcular y retornar el coseno
    res = val / (sr_x * sr_y)
    return res

def RecuperarArchivos():
    col_choice = col_var2.get()
    rep_choice = rep_var2.get()

    # Verificar si el usuario ha seleccionado algo
    if not col_choice or not rep_choice:
        messagebox.showerror("Error", "Por favor, seleccione ambas opciones antes de continuar.")
        return

    col_map = {'Title': 'Title', 'Content': 'Content', 'Title + Content': 'Title_Content', 'Todas': 'Todas'}
    rep_map = {
        'Unigram - Frecuencia': 'unigram_frequency', 'Unigram - Binario': 'unigram_binary', 'Unigram - TF-IDF': 'unigram_tfidf',
        'Bigram - Frecuencia': 'bigram_frequency', 'Bigram - Binario': 'bigram_binary', 'Bigram - TF-IDF': 'bigram_tfidf', 'Todas': None
    }

    # Vectorizar el corpus desde el archivo normalizado
    normalized_file_path2 = file_path_var2.get()
    if not normalized_file_path2:
        messagebox.showerror("Error", "Por favor, cargue primero la prueba normalizado.")
        return
    prueba_df = pd.read_csv(normalized_file_path2)
    
    model_file_path2 = model_pathvar2.get()
    if not model_file_path2:
        messagebox.showerror("Error", "Por favor, verifique que haya seleccionado un modelo.")
        return
    import os
    #path = #f'{model_file_path2}\{col_map[col_choice]}-{rep_map[rep_choice]}.pkl'.replace('_', '-')
    if col_choice == 'Todas':
        
        # Define la ruta de la carpeta
        ruta_carpeta = model_file_path2

        # Recupera todos los nombres de archivos y carpetas en la carpeta
        archivos_y_carpetas = os.listdir(ruta_carpeta)

        # Filtra solo los archivos
        archivos = [f for f in archivos_y_carpetas if os.path.isfile(os.path.join(ruta_carpeta, f))]

        cosenos = {}
        for archivo in archivos:
            path = f'{model_file_path2}/{archivo}'.replace('_', '-')
            print(path)
            
            if (os.path.exists(path)):
	            print ('Ya existe')
	            vector_file = open (path,'rb')
	            X = pickle.load(vector_file)
            else:
                print ('No existe')

            prueba_df['Title_Content'] = prueba_df['Title']

            Y = X.transform(prueba_df['Title'])


            original = pd.read_csv("news_corpus_normalized.csv")
            original.fillna("", inplace=True)
            original['Title_Content'] = original['Title']+" "+original['Content']

           
            if 'Title-Content' in archivo:
                col = 'Title_Content'
            elif 'Title' in archivo and 'Content' not in archivo:
                col = 'Title'
            elif 'Content' in archivo:
                col = 'Content'
            
            H = X.transform(original[col])
            df = pd.DataFrame(H.toarray(), columns=X.get_feature_names_out())
            #print(df)
            #print(pd.DataFrame(Y.toarray(), columns=X.get_feature_names_out()))
            # Convertir X y Y a arrays densos para pasar a la función de coseno
            H_denso = H.toarray()
            Y_denso = Y.toarray()
# Ca           lcular el coseno entre el primer documento de X y Y
            
# It           erar a través de todos los documentos en X
            for i in range(len(H_denso)):
                resultado_coseno = cosine(H_denso[i], Y_denso[0])
                llave = f'{archivo}_{col}_{i+2}'
                cosenos[llave] = resultado_coseno
                print(f'Coseno entre X[{i}] y Y[0]: {resultado_coseno}')
            cosenos_ordenados = dict(sorted(cosenos.items(), key=lambda item: item[1], reverse=True))



            resultado = "\nTop 10 documentos más similares:\n"
            for i, (llave, valor_coseno) in enumerate(cosenos_ordenados.items(), 1):
                if i > 10:  # Limitar a los primeros 10
                    break
                resultado += f'{i}. Documento {llave} - Similaridad (Coseno): {valor_coseno:.4f}\n'
            # Mostrar los resultados en el cuadro de texto
            result_text2.delete(1.0, tk.END)  # Borrar el contenido anterior del cuadro de texto
            result_text2.insert(tk.END, resultado)

    else:
        path = f'{model_file_path2}/{col_map[col_choice]}-{rep_map[rep_choice]}.pkl'.replace('_', '-')
        print(path)

        if(os.path.exists(path)):
	        print ('Ya existe')
	        vector_file = open (path,'rb')
	        X = pickle.load(vector_file)
        else:
            print ('No existe')

        prueba_df['Title_Content'] = prueba_df['Title']

        Y = X.transform(prueba_df[col_map[col_choice]])


        original = pd.read_csv("news_corpus_normalized.csv")
        original.fillna("", inplace=True)
        original['Title_Content'] = original['Title']+" "+original['Content']


        H = X.transform(original[col_map[col_choice]])

        df = pd.DataFrame(H.toarray(), columns=X.get_feature_names_out())
        #print(df)

        #print(pd.DataFrame(Y.toarray(), columns=X.get_feature_names_out()))

        # Convertir X y Y a arrays densos para pasar a la función de coseno
        H_denso = H.toarray()
        Y_denso = Y.toarray()

# Ca    lcular el coseno entre el primer documento de X y Y
        cosenos = {}
# It    erar a través de todos los documentos en X
        for i in range(len(H_denso)):
            resultado_coseno = cosine(H_denso[i], Y_denso[0])
            cosenos[i] = resultado_coseno

            print(f'Coseno entre X[{i}] y Y[0]: {resultado_coseno}')
        cosenos_ordenados = dict(sorted(cosenos.items(), key=lambda item: item[1], reverse=True))



        resultado = "\nTop 10 documentos más similares:\n"
        for i, (indice, valor_coseno) in enumerate(cosenos_ordenados.items(), 1):
            if i > 10:  # Limitar a los primeros 10
                break
            resultado += f'{i}. Documento {indice+2} - Similaridad (Coseno): {valor_coseno:.4f}\n'

        # Mostrar los resultados en el cuadro de texto
        result_text2.delete(1.0, tk.END)  # Borrar el contenido anterior del cuadro de texto
        result_text2.insert(tk.END, resultado) 
    

# Interfaz Segunda ventana

In [5]:
# Interfaz de comparacion 
def load_csv_comparar():
    file_path = filedialog.askopenfilename(filetypes=[("Text files", "*.txt")])
    if file_path:
        columnas = ['Source', 'Title', 'Content', 'Section', 'URL', 'Date']
        df = pd.DataFrame(columns=columnas)
        print(file_path)
        
        with open(file_path, 'r', encoding='utf-8') as file:
            contenido = file.read().replace('\n', ' ')
            print(contenido)
            
        df.loc[0,'Source'] = '0'
        df.loc[0,'Title'] = contenido
        df.loc[0,'Content'] = contenido
        df.loc[0,'Section'] = '0'
        df.loc[0,'URL'] = '0'
        df.loc[0,'Date'] = '0'
        
        df.to_csv('pruebacsv.csv', index=False, quoting=csv.QUOTE_ALL)
        
        normalized_file_path2 = load_and_normalize_csv('pruebacsv.csv')
        if normalized_file_path2:
            file_path_var2.set(normalized_file_path2)
            comparar_button.config(state=tk.NORMAL)

def Selectmodelo():
    # Obtener la lista de carpetas en el directorio actual o en un directorio específico
    directorio_modelos = "./"  # Ajusta esta ruta si los modelos están en otra carpeta
    carpetas_disponibles = [nombre for nombre in os.listdir(directorio_modelos) if os.path.isdir(os.path.join(directorio_modelos, nombre))]

    # Verificar si hay carpetas disponibles
    if not carpetas_disponibles:
        messagebox.showwarning("Advertencia", "No existe ningún modelo creado previamente, puedes crear uno en la ventana anterior.")
        return  # Salir de la función si no hay carpetas disponibles

    # Crear la ventana emergente para mostrar el menú desplegable de carpetas
    ventana = tk.Toplevel()
    ventana.title("Seleccionar Modelo")
    
    # Etiqueta de instrucción
    tk.Label(ventana, text="Seleccione el modelo donde desea buscar:").pack(pady=10)
    
    # Variable para almacenar la selección del usuario
    carpeta_seleccionada = tk.StringVar()

    # Crear un menú desplegable con las carpetas disponibles
    menu_carpetas = ttk.Combobox(ventana, textvariable=carpeta_seleccionada, values=carpetas_disponibles, state="readonly")
    menu_carpetas.pack(pady=10)
    
    # Función para manejar la selección y pasar a la función comparar
    def seleccionar_modelo():
        modelo = carpeta_seleccionada.get()  # Obtener la carpeta seleccionada
        if modelo:  # Si se seleccionó una carpeta
            global PathModel
            PathModel = os.path.join(directorio_modelos, modelo)  # Guardar la ruta completa en PathModel
            ventana.destroy()  # Cerrar la ventana
            try:
                comparar(PathModel)  # Llamar a la función comparar
            except Exception as e:
                messagebox.showerror("Error", f"No se pudo cargar el modelo: {e}")
        else:
            messagebox.showwarning("Advertencia", "No seleccionaste ningún modelo.")
    
    # Botón para confirmar la selección
    ttk.Button(ventana, text="Seleccionar", command=seleccionar_modelo).pack(pady=10)
    


def comparar(pathModel):
    # Cerrar la ventana actual y abrir una nueva ventana
    root.destroy()  # Cierra la ventana actual
    
    messagebox.showinfo("Instrucciones", 
                            '''Si ya cuentas con una prueba normalizada, introduce la direccion de tu archivo, en otro caso presiona el boton Cargar Prueba para normalizar tu archivo''')
    global root2
    root2 = tk.Tk()
    root2.title("Prueba")
    global col_var2
    col_var2 = tk.StringVar()
    global rep_var2
    rep_var2 = tk.StringVar()
    global file_path_var2
    file_path_var2 = tk.StringVar()
    global model_pathvar2
    model_pathvar2 = tk.StringVar()
    
    ttk.Button(root2, text="Cargar Prueba", command=load_csv_comparar).grid(column=0,columnspan=2, row=0, padx=10, pady=10)
    
    ttk.Label(root2, text="Modelo:").grid(column=0, row=1, padx=10, pady=10)
    model_path_entry2 = ttk.Entry(root2, textvariable= model_pathvar2, width=50)
    model_path_entry2.grid(column=1, row=1, padx=10, pady=10)
    model_pathvar2.set(pathModel)
    model_path_entry2.config(state=tk.DISABLED) 
    
    # Ruta del archivo normalizado
    ttk.Label(root2, text="Prueba Normalizada:").grid(column=0, row=2, padx=10, pady=10)
    file_path_entry2 = ttk.Entry(root2, textvariable=file_path_var2, width=50)
    file_path_entry2.grid(column=1, row=2, padx=10, pady=10)
    
    # Desplegables
    ttk.Label(root2, text="Seleccione la Columna a comparar:").grid(column=0, row=3, padx=10, pady=10)
    col_menu2 = ttk.Combobox(root2, textvariable=col_var2, values=['Title', 'Content', 'Title + Content', 'Todas'])
    col_menu2.grid(column=1, row=3, padx=10, pady=10)
    col_menu2.current(0)
    ttk.Label(root2, text="Seleccione Representación:").grid(column=0, row=4, padx=10, pady=10)
    rep_menu2 = ttk.Combobox(root2, textvariable=rep_var2, values=[
        'Unigram - Frecuencia', 'Unigram - Binario', 'Unigram - TF-IDF',
        'Bigram - Frecuencia', 'Bigram - Binario', 'Bigram - TF-IDF'])
    rep_menu2.grid(column=1, row=4, padx=10, pady=10)
    rep_menu2.current(0)
    
    # Botones
    global comparar_button
    comparar_button = ttk.Button(root2, text="Comparar", command=RecuperarArchivos)
    comparar_button.grid(column=1, row=5, padx=10, pady=10)
    comparar_button.config(state=tk.DISABLED)
    
    # Cuadro de resultados
    global result_text2
    result_text2 = tk.Text(root2, height=20, width=80)
    result_text2.grid(column=0, row=6, columnspan=3, padx=10, pady=10)


# Interfaz primer ventana

In [6]:
# Función de selección de la interfaz
def analyze_data():
    col_choice = col_var.get()
    rep_choice = rep_var.get()

    # Verificar si el usuario ha seleccionado algo
    if not col_choice or not rep_choice:
        messagebox.showerror("Error", "Por favor, seleccione ambas opciones antes de continuar.")
        return

    col_map = {'Title': 'Title', 'Content': 'Content', 'Title + Content': 'Title_Content'}
    rep_map = {
        'Unigram - Frecuencia': 'unigram_frequency', 'Unigram - Binario': 'unigram_binary', 'Unigram - TF-IDF': 'unigram_tfidf',
        'Bigram - Frecuencia': 'bigram_frequency', 'Bigram - Binario': 'bigram_binary', 'Bigram - TF-IDF': 'bigram_tfidf', 'Todas': None
    }

    # Vectorizar el corpus desde el archivo normalizado
    normalized_file_path = file_path_var.get()
    if not normalized_file_path:
        messagebox.showerror("Error", "Por favor, cargue primero el archivo normalizado.")
        return
    
    corpus_df = pd.read_csv(normalized_file_path)
    global vectorizations
    vectorizations = vectorize_corpus(corpus_df)
    
    result = show_representations(vectorizations, col_map[col_choice], rep_map[rep_choice])
    result_text.delete(1.0, tk.END)
    result_text.insert(tk.END, result)

# Función para guardar todas las representaciones en archivos PKL
#def save_all_vectorizations():
#    save_all_vectorizations_to_pkl(vectorizations,nombre)
#    next_button.config(state=tk.NORMAL)

def save_all_vectorizations():
    while True:
        # Crear una ventana emergente para pedir el nombre de la carpeta
        nombre_carpeta = simpledialog.askstring("Guardar Vectorizaciones", "Introduce el nombre de la carpeta para guardar los archivos:")
        
        if not nombre_carpeta:
            # Si el usuario no introduce un nombre, mostrar un mensaje de advertencia
            messagebox.showwarning("Advertencia", "No se introdujo ningún nombre de carpeta.")
            return  # Salir de la función si no se introduce ningún nombre
        
        # Verificar si la carpeta ya existe
        if os.path.exists(nombre_carpeta):
            # Preguntar si quiere sobrescribir la carpeta existente
            overwrite = messagebox.askyesno("Carpeta existente", 
                                            f"La carpeta '{nombre_carpeta}' ya existe. ¿Deseas sobrescribirla?")
            if overwrite:
                # Si acepta sobrescribir, romper el bucle y continuar
                break
            else:
                # Si no quiere sobrescribir, volver a preguntar por otro nombre
                continue
        else:
            # Si la carpeta no existe, crearla
            os.makedirs(nombre_carpeta)
            break  # Salir del bucle si la carpeta fue creada correctamente
    
    try:
        # Llamar a la función para guardar las vectorizaciones (usando el nombre de la carpeta)
        save_all_vectorizations_to_pkl(vectorizations, nombre_carpeta)
        
    except Exception as e:
        messagebox.showerror("Error", f"No se pudo crear la carpeta: {e}")
        
# Función para mostrar las representaciones
def show_representations(vectorizations, col, vec_type=None):
    if vec_type:
        return vectorizations[col][vec_type][1]
    else:
        result = ""
        for key, value in vectorizations[col].items():
            result += f"\n--- {key.replace('_', ' ').title()} ---\n{value}\n"
        return result

# Función para cargar el archivo CSV
def load_csv():
    file_path = filedialog.askopenfilename(filetypes=[("CSV files", "*.csv")])
    if file_path:
        normalized_file_path = load_and_normalize_csv(file_path)
        if normalized_file_path:
            file_path_var.set(normalized_file_path)
           
def Inicio():
# Interfaz gráfica 

    messagebox.showinfo("Bienvenido", 
                            "Si quieres realizar una comparación con una representación previamente guardada, "
                            "oprime el botón siguiente. En otro caso, crea tu propia representación.")
    global root
    root = tk.Tk()
    root.title("Análisis de Representaciones Vectoriales")
    global col_var
    col_var = tk.StringVar()
    global rep_var
    rep_var = tk.StringVar()
    global file_path_var
    file_path_var = tk.StringVar()

    
    ttk.Button(root, text="Cargar CSV y Normalizar", command=load_csv).grid(column=0,columnspan=2, row=0, padx=10, pady=10)

    # Ruta del archivo normalizado
    ttk.Label(root, text="Archivo Normalizado:").grid(column=0, row=1, padx=10, pady=10)
    file_path_entry = ttk.Entry(root, textvariable=file_path_var, width=50)
    file_path_entry.grid(column=1, row=1, padx=10, pady=10)

    # Desplegables
    ttk.Label(root, text="Seleccione Columna:").grid(column=0, row=2, padx=10, pady=10)
    col_menu = ttk.Combobox(root, textvariable=col_var, values=['Title', 'Content', 'Title + Content'])
    col_menu.grid(column=1, row=2, padx=10, pady=10)
    col_menu.current(0)

    ttk.Label(root, text="Seleccione Representación:").grid(column=0, row=3, padx=10, pady=10)
    rep_menu = ttk.Combobox(root, textvariable=rep_var, values=[
        'Unigram - Frecuencia', 'Unigram - Binario', 'Unigram - TF-IDF',
        'Bigram - Frecuencia', 'Bigram - Binario', 'Bigram - TF-IDF', 'Todas'])
    rep_menu.grid(column=1, row=3, padx=10, pady=10)
    rep_menu.current(0)

    # Botones
    analyze_button = ttk.Button(root, text="Analizar", command=analyze_data)
    analyze_button.grid(column=1, row=4, padx=10, pady=10)

    next_button = ttk.Button(root, text="siguiente", command=Selectmodelo)
    next_button.grid(column=2, row=7, padx=10, pady = 10)
    #next_button.config(state=tk.DISABLED)

    save_button = ttk.Button(root, text="Guardar Todas las Vectorizaciones", command=save_all_vectorizations)
    save_button.grid(column=0, row=7, columnspan=2, padx=10, pady=10)

    # Cuadro de resultados
    global result_text
    result_text = tk.Text(root, height=20, width=80)
    result_text.grid(column=0, row=6, columnspan=3, padx=10, pady=10)
    root.mainloop()


In [7]:
Inicio()

2024-10-18 11:05:30.798 python[9558:566077] +[IMKClient subclass]: chose IMKClient_Legacy
2024-10-18 11:05:30.798 python[9558:566077] +[IMKInputSession subclass]: chose IMKInputSession_Legacy
2024-10-18 11:05:33.628 python[9558:566077] The class 'NSOpenPanel' overrides the method identifier.  This method is implemented by class 'NSWindow'


/Users/sebastianloeza/Desktop/Escuela/6to/NLP/Practicas/Practica3/Similitud_archivos/Pruebas/Sehainbaum_contenido_pacial.txt
presidenta Claudia Sheinbaum 


./PruebaProfe/Title-unigram-frequency.pkl
Ya existe
val:  0
x:  3.0
y:  1.4142135623730951
Coseno entre X[0] y Y[0]: 0.0
val:  0
x:  2.6457513110645907
y:  1.4142135623730951
Coseno entre X[1] y Y[0]: 0.0
val:  0
x:  3.0
y:  1.4142135623730951
Coseno entre X[2] y Y[0]: 0.0
val:  0
x:  2.6457513110645907
y:  1.4142135623730951
Coseno entre X[3] y Y[0]: 0.0
val:  0
x:  2.0
y:  1.4142135623730951
Coseno entre X[4] y Y[0]: 0.0
val:  0
x:  2.23606797749979
y:  1.4142135623730951
Coseno entre X[5] y Y[0]: 0.0
val:  0
x:  2.6457513110645907
y:  1.4142135623730951
Coseno entre X[6] y Y[0]: 0.0
val:  0
x:  2.449489742783178
y:  1.4142135623730951
Coseno entre X[7] y Y[0]: 0.0
val:  0
x:  2.6457513110645907
y:  1.4142135623730951
Coseno entre X[8] y Y[0]: 0.0
val:  0
x:  2.23606797749979
y:  1.4142135623730951
Coseno entre X[9] y Y[0]: 0.0
val:  0
x:  2.6457513110645907
y:  1.4142135623730951
Coseno entre X[10] y Y[0]: 0.0
val:  0
x:  2.449489742783178
y:  1.4142135623730951
Coseno entre X[11] y

/var/folders/4w/0qtssn4s1_bck4zfcq9k819c0000gn/T/ipykernel_9558/4232300062.py:10: RuntimeWarning: invalid value encountered in divide
  res = val / (sr_x * sr_y)


y:  1.0
Coseno entre X[170] y Y[0]: 0.0
val:  0
x:  7.615773105863909
y:  1.0
Coseno entre X[171] y Y[0]: 0.0
val:  0
x:  3.7416573867739413
y:  1.0
Coseno entre X[172] y Y[0]: 0.0
val:  0
x:  3.872983346207417
y:  1.0
Coseno entre X[173] y Y[0]: 0.0
val:  0
x:  4.123105625617661
y:  1.0
Coseno entre X[174] y Y[0]: 0.0
val:  0
x:  3.1622776601683795
y:  1.0
Coseno entre X[175] y Y[0]: 0.0
val:  0
x:  3.3166247903554
y:  1.0
Coseno entre X[176] y Y[0]: 0.0
val:  0
x:  4.47213595499958
y:  1.0
Coseno entre X[177] y Y[0]: 0.0
val:  0
x:  4.358898943540674
y:  1.0
Coseno entre X[178] y Y[0]: 0.0
val:  0
x:  4.242640687119285
y:  1.0
Coseno entre X[179] y Y[0]: 0.0
val:  0
x:  3.4641016151377544
y:  1.0
Coseno entre X[180] y Y[0]: 0.0
val:  0
x:  4.0
y:  1.0
Coseno entre X[181] y Y[0]: 0.0
val:  0
x:  4.0
y:  1.0
Coseno entre X[182] y Y[0]: 0.0
val:  0
x:  4.123105625617661
y:  1.0
Coseno entre X[183] y Y[0]: 0.0
val:  0
x:  0.0
y:  1.0
Coseno entre X[184] y Y[0]: 0
val:  0
x:  5.6568542494

...

val:  0
x:  5.385164807134504
y:  3.0
Coseno entre X[186] y Y[0]: 0.0
val:  2
x:  5.656854249492381
y:  3.0
Coseno entre X[187] y Y[0]: 0.1178511301977579
val:  1
x:  5.385164807134504
y:  3.0
Coseno entre X[188] y Y[0]: 0.061898446059017294
val:  0
x:  6.244997998398398
y:  3.0
Coseno entre X[189] y Y[0]: 0.0
val:  1
x:  5.477225575051661
y:  3.0
Coseno entre X[190] y Y[0]: 0.06085806194501846
val:  0
x:  4.358898943540674
y:  3.0
Coseno entre X[191] y Y[0]: 0.0
val:  0
x:  4.123105625617661
y:  3.0
Coseno entre X[192] y Y[0]: 0.0
val:  0
x:  4.795831523312719
y:  3.0
Coseno entre X[193] y Y[0]: 0.0
val:  0
x:  4.0
y:  3.0
Coseno entre X[194] y Y[0]: 0.0
val:  0
x:  5.291502622129181
y:  3.0
Coseno entre X[195] y Y[0]: 0.0
val:  1
x:  4.898979485566356
y:  3.0
Coseno entre X[196] y Y[0]: 0.06804138174397717
val:  0
x:  6.324555320336759
y:  3.0
Coseno entre X[197] y Y[0]: 0.0
val:  0
x:  5.656854249492381
y:  3.0
Coseno entre X[198] y Y[0]: 0.0
val:  0
x:  4.58257569495584
y:  3.0
Cos

/var/folders/4w/0qtssn4s1_bck4zfcq9k819c0000gn/T/ipykernel_9558/4232300062.py:10: RuntimeWarning: invalid value encountered in divide
  res = val / (sr_x * sr_y)


x:  3.872983346207417
y:  1.7320508075688772
Coseno entre X[173] y Y[0]: 0.0
val:  0
x:  4.123105625617661
y:  1.7320508075688772
Coseno entre X[174] y Y[0]: 0.0
val:  0
x:  3.1622776601683795
y:  1.7320508075688772
Coseno entre X[175] y Y[0]: 0.0
val:  0
x:  3.3166247903554
y:  1.7320508075688772
Coseno entre X[176] y Y[0]: 0.0
val:  0
x:  4.47213595499958
y:  1.7320508075688772
Coseno entre X[177] y Y[0]: 0.0
val:  0
x:  4.358898943540674
y:  1.7320508075688772
Coseno entre X[178] y Y[0]: 0.0
val:  0
x:  4.242640687119285
y:  1.7320508075688772
Coseno entre X[179] y Y[0]: 0.0
val:  0
x:  3.4641016151377544
y:  1.7320508075688772
Coseno entre X[180] y Y[0]: 0.0
val:  0
x:  4.0
y:  1.7320508075688772
Coseno entre X[181] y Y[0]: 0.0
val:  0
x:  4.0
y:  1.7320508075688772
Coseno entre X[182] y Y[0]: 0.0
val:  0
x:  4.123105625617661
y:  1.7320508075688772
Coseno entre X[183] y Y[0]: 0.0
val:  0
x:  0.0
y:  1.7320508075688772
Coseno entre X[184] y Y[0]: 0
val:  0
x:  5.656854249492381
y: 

/var/folders/4w/0qtssn4s1_bck4zfcq9k819c0000gn/T/ipykernel_9558/4232300062.py:10: RuntimeWarning: invalid value encountered in scalar divide
  res = val / (sr_x * sr_y)


y:  1.0
Coseno entre X[327] y Y[0]: 0.01298552420434238
val:  0.0
x:  0.9999999999999999
y:  1.0
Coseno entre X[328] y Y[0]: 0.0
val:  0.0
x:  0.9999999999999999
y:  1.0
Coseno entre X[329] y Y[0]: 0.0
val:  0.0
x:  1.0
y:  1.0
Coseno entre X[330] y Y[0]: 0.0
val:  0.013386711298024252
x:  1.0
y:  1.0
Coseno entre X[331] y Y[0]: 0.013386711298024252
val:  0.0
x:  0.9999999999999999
y:  1.0
Coseno entre X[332] y Y[0]: 0.0
val:  0.017699253033510665
x:  1.0000000000000002
y:  1.0
Coseno entre X[333] y Y[0]: 0.01769925303351066
val:  0.03675181876927611
x:  1.0
y:  1.0
Coseno entre X[334] y Y[0]: 0.03675181876927611
val:  0.057145378740753185
x:  0.9999999999999998
y:  1.0
Coseno entre X[335] y Y[0]: 0.0571453787407532
val:  0.0
x:  0.9999999999999997
y:  1.0
Coseno entre X[336] y Y[0]: 0.0
val:  0.05895723237123615
x:  1.0
y:  1.0
Coseno entre X[337] y Y[0]: 0.05895723237123615
val:  0.0
x:  0.9999999999999999
y:  1.0
Coseno entre X[338] y Y[0]: 0.0
val:  0.0
x:  0.9999999999999999
y:  1

In [8]:
vectorizations['Title']['unigram_frequency'][1]

NameError: name 'vectorizations' is not defined

: 